**With Amazon Redshift ML**, you can now leverage Amazon Forecast, a machine-learning based  time-series forecasting service, without learning any new tools or having to create pipelines to  move your data. You can use SQL statements to create and train forecasting models from your time series data in Amazon Redshift and use these models to generate forecasts about revenue,inventory, resource usage, or demand forecasting in your queries and reports.

**Prerequisites**

Below are the prerequisites that you need to consider before starting:
a) On the Amazon S3 console, create an S3 bucket that Redshift ML uses for uploading the
training data that Forecast uses to train the model.
b) Create an AWS Identity and Access Management (IAM role) using the Redshift console ,
read more at [Creating IAM role](https://docs.aws.amazon.com/redshift/latest/mgmt/default-iam-role.html#create-iam) as default role Although it’s easy to get started with AmazonS3FullAccess , AmazonForecastFullAccess, AmazonRedshiftAllCommandsFullAccess and AmazonSageMakerFullAccess .

**Load Sample Data**

In [0]:
create table bike_sampledata
(
event_timestamp timestamp,
season float , 
holiday float , 
workingday float , 
weather float , 
temperature float , 
atemperature float, 
humidity float , 
windspeed float , 
casual float , 
registered float , 
target float,
item_id varchar(255)
);

copy bike_sampledata
from 's3://redshift-blogs/amazon-forecast-blog/bike-data/bike.csv'
IAM_ROLE default
format as csv
region 'us-east-1';

**Create Forecast Model**

For Redshift ML forecasting model, you need to ensure that when you issue a CREATE MODEL statement specify MODEL_TYPE as FORECAST. When Redshift ML trains a model or predictor on Amazon Forecast it has a fixed forecast meaning there is not a physical model to compile and execute. Thus, an inference function is not needed for FORECAST models. Instead, we will show you below how you can pull an exported forecast from the training output location in Amazon S3 into a table locally in your Amazon Redshift data warehouse.

In [0]:
DROP MODEL forecast_bike_consumption;

CREATE MODEL forecast_bike_consumption 
FROM (
     select
     s.item_id , s.event_timestamp, s.target , s.workingday
     from     
     bike_sampledata s
     )
TARGET target 
IAM_ROLE 'arn:aws:iam::984077116443:role/service-role/AmazonRedshift-CommandsAccessRole-20220415T163911'
-- please change ARN To the Redshift cluster IAM Role. For preview default in the IAM_ROLE s not supported 
AUTO ON MODEL_TYPE FORECAST
OBJECTIVE 'AverageWeightedQuantileLoss'
SETTINGS (S3_BUCKET 'ab-demo-dwhmod',
          HORIZON 24,
          FREQUENCY 'H',
          PERCENTILES '0.25,0.50,0.75,mean',
          S3_GARBAGE_COLLECT ON);

In above craete model command model name is “forecast_electricity_consumption”. We are using the below setting for creating the model: 
-	**Target**: Name of the field for prediction. 
-	**HORIZON**: Number of time-steps in the future to forecast. 
-	**FREQUENCY**: Forecast frequency e.g., ‘H’ meaning hourly. the frequency for the predictions must match the frequency of the input data. Available options are Y | M | W | D | H | 30min | 15min | 10min | 5min | 1min. It’s required if training a forecast model.
- **PERCENTILES** (Optional) : A comma-delimited string that specifies the forecast types used to train a predictor. Forecast types can be quantiles from 0.01 to 0.99, in increments of 0.01 or higher. You can also specify the mean forecast with mean. You can specify a maximum of five forecast types.

**Check Model Status**

Create Model command is run in synchronous mode meaning after command is run it will take 10-15 minutes to setup the required Amazon forecast artifacts and then will start the training in Asynchronous mode e.g., model training is done behind the scenes by Amazon Forecast. You can check if model is in Ready state by running show model command. 

Model is trained and deployed when status is shown as “READY”. If you see “TRAINING” that means model is still under training and you need to wait for it to complete. Training time depends on amount of data.

In [0]:
SHOW MODEL forecast_bike_consumption;

**Generating Forecast**

After a model has finished training, you can run a simple CTAS command to instantiate all the forecast results into a table. This command will get all the forecast results from Amazon S3 bucket where Amazon Forecast exported results

In [0]:
CREATE TABLE forecast_bike_consumption_results 
AS SELECT FORECAST(forecast_bike_consumption);

**Checking Forecast Results**

we ran forecast model to get forecast for next 24 hours , we can valicate the results as follows

In [0]:
select * from forecast_bike_consumption_results;